Note: this won't work on your system unless you download the datasets and order them in the same way I have

In [22]:
import pandas as pd
import numpy as np
import io
import os
import altair as alt

In [23]:
# Import datetime so we can treat date columns as such and perform operations
from datetime import datetime as dt

Imports of packages

In [24]:
#os.chdir("C:\\Users\\Alexa\\OneDrive\\Ottawa U\\Year 4\\Fall\\MAT4376 - Data Analysis\\Project 1")
# set this to wherever the provided dataset is located

In [25]:
os.getcwd()

'C:\\Users\\awyat049\\OneDrive\\Ottawa U\\Year 4\\Fall\\MAT4376 - Data Analysis\\Project 1\\MAT4376-P1'

In [26]:
as_data = pd.read_csv('polls_us_election_2016.csv')

In [27]:
whole_data = pd.read_csv('Dataset_assigned_data_taken_from/president_general_polls_2016.csv')

In [28]:
poll_raw_years = pd.read_csv('2016_Pollster_Ratings/raw-polls.csv')

In [29]:
poll_ratings_bias = pd.read_csv('2016_Pollster_Ratings/pollster-stats-full.csv')

In [123]:
pres_pop = pd.read_csv('2016_pres_pop_vote.csv', index_col=0).dropna()

In [130]:
# Sample View
#pres_pop#.loc['Arizona','Trump_Pct']

In [30]:
poll_raw_years.columns

Index(['poll_id', 'question_id', 'race_id', 'year', 'race', 'location',
       'type_simple', 'type_detail', 'pollster', 'pollster_rating_id',
       'methodology', 'partisan', 'polldate', 'samplesize', 'cand1_name',
       'cand1_id', 'cand1_party', 'cand1_pct', 'cand2_name', 'cand2_id',
       'cand2_party', 'cand2_pct', 'cand3_pct', 'margin_poll', 'electiondate',
       'cand1_actual', 'cand2_actual', 'margin_actual', 'error', 'bias',
       'rightcall', 'advancedplusminus', 'comment'],
      dtype='object')

In [31]:
# convert all dates into datetime format
as_data['startdate'] = as_data['startdate'].astype('datetime64')
as_data['enddate'] = as_data['enddate'].astype('datetime64')
whole_data['startdate'] = whole_data['startdate'].astype('datetime64')
whole_data['enddate'] = whole_data['enddate'].astype('datetime64')
# Note: forecast date in whole_data is WRONG - interpreted month as year
poll_raw_years['polldate'] = poll_raw_years['polldate'].astype('datetime64')
poll_raw_years['electiondate'] = poll_raw_years['electiondate'].astype('datetime64')

In [32]:
#only 2016 polls

poll_raw_years = poll_raw_years[poll_raw_years['year'] == 2016]
poll_raw_years['electiondate'].unique

<bound method Series.unique of 7634   2016-02-01
7635   2016-02-01
7636   2016-02-01
7637   2016-02-01
7638   2016-02-01
          ...    
9003   2016-11-08
9004   2016-12-10
9005   2016-12-10
9006   2016-12-10
9007   2016-12-10
Name: electiondate, Length: 1374, dtype: datetime64[ns]>

In [33]:
# match pols from 'whole_data' and 'poll_raw_years'
# first cut down 'poll_raw_years' to just 2016 and just November Elections


poll_raw_years = poll_raw_years[poll_raw_years['electiondate'] == np.datetime64('2016-11-08')]

#contributor_polls = poll_raw_years[poll_raw_years['pollster']=='Gravis Marketing/Kaplan Strategies']
#contributor_polls
poll_raw_years = poll_raw_years[poll_raw_years['type_simple'] == 'Pres-G']
poll_raw_years.columns

Index(['poll_id', 'question_id', 'race_id', 'year', 'race', 'location',
       'type_simple', 'type_detail', 'pollster', 'pollster_rating_id',
       'methodology', 'partisan', 'polldate', 'samplesize', 'cand1_name',
       'cand1_id', 'cand1_party', 'cand1_pct', 'cand2_name', 'cand2_id',
       'cand2_party', 'cand2_pct', 'cand3_pct', 'margin_poll', 'electiondate',
       'cand1_actual', 'cand2_actual', 'margin_actual', 'error', 'bias',
       'rightcall', 'advancedplusminus', 'comment'],
      dtype='object')

In [34]:
whole_data.columns

Index(['cycle', 'branch', 'type', 'matchup', 'forecastdate', 'state',
       'startdate', 'enddate', 'pollster', 'grade', 'samplesize', 'population',
       'poll_wt', 'rawpoll_clinton', 'rawpoll_trump', 'rawpoll_johnson',
       'rawpoll_mcmullin', 'adjpoll_clinton', 'adjpoll_trump',
       'adjpoll_johnson', 'adjpoll_mcmullin', 'multiversions', 'url',
       'poll_id', 'question_id', 'createddate', 'timestamp'],
      dtype='object')

In [35]:
# select all cells from original set that have a 'poll_id', 'question_id', 'samplesize'

final_matched_set = whole_data[whole_data['poll_id'].isin(poll_raw_years['poll_id'].unique())]
final_matched_set

cycle     branch        type                        matchup  \
0       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
1       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
2       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
3       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
4       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
...      ...        ...         ...                            ...   
10711   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
10726   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
10729   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
10800   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
11071   2016  President  polls-only  Clinton vs. Trump vs. Johnson   

      forecastdate           state  startdate    enddate  \
0          11/8/16            U.S. 2016-11-03 2016-11-06   
1          11/8/16            U.S. 2016-11-01 2016-11-07   
2          11/8/16            U.S. 2016-11-02 2016-11-06   
3          11/8/16            U.S. 2016-11-04 2016-11-07   
4          11/8/16            U.S. 2016-11-03 2016-11-06   
...            ...             ...        ...        ...   
10711      11/8/16         Florida 2016-10-25 2016-10-31   
10726      11/8/16        Michigan 2016-10-25 2016-10-31   
10729      11/8/16  North Carolina 2016-10-25 2016-10-31   
10800      11/8/16            U.S. 2016-10-18 2016-10-20   
11071      11/8/16            U.S. 2016-10-17 2016-10-23   

                       pollster grade  ...  adjpoll_clinton adjpoll_trump  \
0      ABC News/Washington Post    A+  ...         45.20163      41.72430   
1       Google Consumer Surveys     B  ...         43.34557      41.21439   
2                         Ipsos    A-  ...         42.02638      38.81620   
3                        YouGov     B  ...         45.65676      40.92004   
4              Gravis Marketing    B-  ...         46.84089      42.33184   
...                         ...   ...  ...              ...           ...   
10711              SurveyMonkey    C-  ...         44.64055      45.48589   
10726              SurveyMonkey    C-  ...         41.64558      42.50747   
10729              SurveyMonkey    C-  ...         45.62324      44.41153   
10800  The Times-Picayune/Lucid   NaN  ...         45.34765      41.99739   
11071              SurveyMonkey    C-  ...         44.56214      42.97135   

       adjpoll_johnson  adjpoll_mcmullin  multiversions  \
0             4.626221               NaN            NaN   
1             5.175792               NaN            NaN   
2             6.844734               NaN            NaN   
3             6.069454               NaN            NaN   
4             3.726098               NaN            NaN   
...                ...               ...            ...   
10711         2.020044               NaN            NaN   
10726         5.020043               NaN            NaN   
10729         4.020043               NaN            NaN   
10800         3.061498               NaN            NaN   
11071         3.088467               NaN            NaN   

                                                     url  poll_id  \
0      https://www.washingtonpost.com/news/the-fix/wp...    48630   
1      https://datastudio.google.com/u/0/#/org//repor...    48847   
2      http://projects.fivethirtyeight.com/polls/2016...    48922   
3      https://d25d2506sfb94s.cloudfront.net/cumulus_...    48687   
4      http://www.gravispolls.com/2016/11/final-natio...    48848   
...                                                  ...      ...   
10711  https://www.surveymonkey.com/elections/map?pol...    47892   
10726  https://www.surveymonkey.com/elections/map?pol...    47905   
10729  https://www.surveymonkey.com/elections/map?pol...    47916   
10800          https://luc.id/2016-presidential-tracker/    47163   
11071  https://www.scribd.com/document/328753246/NBC

In [36]:
final_matched_set = final_matched_set[final_matched_set['question_id'].isin(poll_raw_years['question_id'].unique())]
final_matched_set.head(10)

cycle     branch        type                        matchup forecastdate  \
1    2016  President  polls-plus  Clinton vs. Trump vs. Johnson      11/8/16   
2    2016  President  polls-plus  Clinton vs. Trump vs. Johnson      11/8/16   
3    2016  President  polls-plus  Clinton vs. Trump vs. Johnson      11/8/16   
4    2016  President  polls-plus  Clinton vs. Trump vs. Johnson      11/8/16   
8    2016  President  polls-plus  Clinton vs. Trump vs. Johnson      11/8/16   
9    2016  President  polls-plus  Clinton vs. Trump vs. Johnson      11/8/16   
10   2016  President  polls-plus  Clinton vs. Trump vs. Johnson      11/8/16   
11   2016  President  polls-plus  Clinton vs. Trump vs. Johnson      11/8/16   
15   2016  President  polls-plus  Clinton vs. Trump vs. Johnson      11/8/16   
16   2016  President  polls-plus  Clinton vs. Trump vs. Johnson      11/8/16   

         state  startdate    enddate                  pollster grade  ...  \
1         U.S. 2016-11-01 2016-11-07   Google Consumer Surveys     B  ...   
2         U.S. 2016-11-02 2016-11-06                     Ipsos    A-  ...   
3         U.S. 2016-11-04 2016-11-07                    YouGov     B  ...   
4         U.S. 2016-11-03 2016-11-06          Gravis Marketing    B-  ...   
8   New Mexico 2016-11-06 2016-11-06                  Zia Poll   NaN  ...   
9         U.S. 2016-11-04 2016-11-07                  IBD/TIPP    A-  ...   
10        U.S. 2016-11-04 2016-11-06          Selzer & Company    A+  ...   
11        U.S. 2016-11-01 2016-11-04         Angus Reid Global    A-  ...   
15        Iowa 2016-11-01 2016-11-04          Selzer & Company    A+  ...   
16        U.S. 2016-11-05 2016-11-07  The Times-Picayune/Lucid   NaN  ...   

    adjpoll_clinton adjpoll_trump  adjpoll_johnson  adjpoll_mcmullin  \
1          43.34557      41.21439         5.175792               NaN   
2          42.02638      38.81620         6.844734               NaN   
3          45.65676      40.92004         6.069454               NaN   
4          46.84089      42.33184         3.726098               NaN   
8          44.82594      41.59978         7.870127               NaN   
9          42.92745      42.23545         6.316175               NaN   
10         44.21714      40.57082         4.068708               NaN   
11         47.57171      43.68125         5.556625               NaN   
15         39.37561      45.66917         6.062713               NaN   
16         45.13966      42.26495         3.679914               NaN   

    multiversions                                                url  poll_id  \
1             NaN  https://datastudio.google.com/u/0/#/org//repor...    48847   
2             NaN  http://projects.fivethirtyeight.com/polls/2016...    48922   
3             NaN  https://d25d2506sfb94s.cloudfront.net/cumulus_...    48687   
4             NaN  http://www.gravispolls.com/2016/11/final-natio...    48848   
8             NaN  http://projects.fivethirtyeight.com.s3.amazona...    48614   
9             NaN  http://www.investors.com/politics/ibd-tipp-pre...    48916   
10            NaN  http://www.bloomberg.com/politics/articles/201...    48513   
11            NaN  http://angusreid.org/wp-content/uploads/2016/1...    48626   
15            NaN  http://www.desmoinesregister.com/story/news/po...    48470   
16            NaN          https://luc.id/2016-presidential-tracker/    48771   

    question_id  createddate             timestamp  
1         76443      11/7/16  09:35:33  8 Nov 2016  
2         76636      11/8/16  09:35:33  8 Nov 2016  
3         76262      11/7/16  09:35:33  8 Nov 2016  
4         76444      11/7/16  09:35:33  8 Nov 2016  
8         76158      11/7/16  09:35:33  8 Nov 2016  
9         76611      11/8/16  09:35:33  8 Nov 2016  
10        76036      11/7/16  09:35:33  8 Nov 2016  
11        76181      11/7/16  09:35:33  8 Nov 2016  
15        75957      11/5/16  09:35:33  8 Nov 2016  
16        76354      11/7/16  09:35:33  8 Nov 2016  

[10 ro

Import assigned data

In [37]:
#final_matched_set.loc[8]
final_matched_set.shape[0]
final_matched_set = final_matched_set.reset_index()
final_matched_set
#final_matched_set.iloc[8]

index  cycle     branch        type                        matchup  \
0         1   2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
1         2   2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
2         3   2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
3         4   2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
4         8   2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
...     ...    ...        ...         ...                            ...   
1252  10711   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
1253  10726   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
1254  10729   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
1255  10800   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
1256  11071   2016  President  polls-only  Clinton vs. Trump vs. Johnson   

     forecastdate           state  startdate    enddate  \
0         11/8/16            U.S. 2016-11-01 2016-11-07   
1         11/8/16            U.S. 2016-11-02 2016-11-06   
2         11/8/16            U.S. 2016-11-04 2016-11-07   
3         11/8/16            U.S. 2016-11-03 2016-11-06   
4         11/8/16      New Mexico 2016-11-06 2016-11-06   
...           ...             ...        ...        ...   
1252      11/8/16         Florida 2016-10-25 2016-10-31   
1253      11/8/16        Michigan 2016-10-25 2016-10-31   
1254      11/8/16  North Carolina 2016-10-25 2016-10-31   
1255      11/8/16            U.S. 2016-10-18 2016-10-20   
1256      11/8/16            U.S. 2016-10-17 2016-10-23   

                      pollster  ... adjpoll_clinton  adjpoll_trump  \
0      Google Consumer Surveys  ...        43.34557       41.21439   
1                        Ipsos  ...        42.02638       38.81620   
2                       YouGov  ...        45.65676       40.92004   
3             Gravis Marketing  ...        46.84089       42.33184   
4                     Zia Poll  ...        44.82594       41.59978   
...                        ...  ...             ...            ...   
1252              SurveyMonkey  ...        44.64055       45.48589   
1253              SurveyMonkey  ...        41.64558       42.50747   
1254              SurveyMonkey  ...        45.62324       44.41153   
1255  The Times-Picayune/Lucid  ...        45.34765       41.99739   
1256              SurveyMonkey  ...        44.56214       42.97135   

     adjpoll_johnson  adjpoll_mcmullin  multiversions  \
0           5.175792               NaN            NaN   
1           6.844734               NaN            NaN   
2           6.069454               NaN            NaN   
3           3.726098               NaN            NaN   
4           7.870127               NaN            NaN   
...              ...               ...            ...   
1252        2.020044               NaN            NaN   
1253        5.020043               NaN            NaN   
1254        4.020043               NaN            NaN   
1255        3.061498               NaN            NaN   
1256        3.088467               NaN            NaN   

                                                    url  poll_id  question_id  \
0     https://datastudio.google.com/u/0/#/org//repor...    48847        76443   
1     http://projects.fivethirtyeight.com/polls/2016...    48922        76636   
2     https://d25d2506sfb94s.cloudfront.net/cumulus_...    48687        76262   
3     http://www.gravispolls.com/2016/11/final-natio...    48848        76444   
4     http://projects.fivethirtyeight.com.s3.amazona...    48614        76158   
...                                                 ...      ...          ...   
1252  https://www.surveymonkey.com/elections/map?pol...    47892        74948   
1253  https://www.surveymonkey.com/elections/map?pol...    47905        74961   
1254  https://www.surveymonkey.com/elections/map?pol...    47916        74972   
1255          https://luc.id/2016-presidential-t

# ADD IN BIAS BELOW HERE
- recall: bias is calculated after the election
- will calculate bias myself

In [38]:
poll_raw_years_indices = [[].copy() for i in range(final_matched_set.shape[0])]
matching_pollsters = [[].copy() for i in range(final_matched_set.shape[0])]
matching_methodology = [0]*final_matched_set.shape[0]#[].copy() for i in range(final_matched_set.shape[0])]
matching_bias = [[].copy() for i in range(final_matched_set.shape[0])]

i = 0

count = 0

# note: index is the LABELLED index
for index, row in final_matched_set.iterrows():
    
    poll_raw_years_indices[i] = poll_raw_years.index[poll_raw_years['poll_id'] == row['poll_id']].tolist()[0]
    
    matching_pollsters[i] = (poll_raw_years.loc[poll_raw_years_indices[i]])['pollster']
    matching_methodology[i] = (poll_raw_years.loc[poll_raw_years_indices[i]])['methodology']
    
    #if poll_raw_years.index[poll_raw_years['poll_id'] == row['poll_id']].tolist()[0] in poll_raw_years_indices[:i-1]:
    if (row)['question_id'] == poll_raw_years.loc[poll_raw_years_indices[i]]['question_id']:
            #not sure if correct
        count += 1
    
    #for j in range(len(poll_raw_years_indices[i])):
        
        # None with more than one matching index
        #if j > 0:
            #print("more than one")
        
        #print(str((final_matched_set.loc[index])['question_id']) + " : " + str(poll_raw_years.loc[poll_raw_years_indices[i][j]]['question_id']))
        #print(str((final_matched_set.loc[index])['samplesize']) + " : " + str(poll_raw_years.loc[poll_raw_years_indices[i][j]]['samplesize']))
        
        #if (final_matched_set.loc[index])['question_id'] != poll_raw_years.loc[poll_raw_years_indices[i][j]]['question_id']:
            #final_matched_set.drop(index = index)
            
            
        #elif (final_matched_set.loc[index])['samplesize'] != poll_raw_years.loc[poll_raw_years_indices[i][j]]['samplesize']:
            #final_matched_set.drop(index = index)
    i += 1

#for i in poll_raw_years_indices:
    

print("Number of Doubles: " + str(count))
print("done")
    
# now it's confirmed that all our rows are correct, so next within the same code APPEND THE PROPER CELL FOR METHODOLOGY 
## Will need to use the strategy of making a new list then appaending that list as a column

#indices = whole_data.index[whole_data['poll_id'].isin()]

#need to find the index in poll_raw_years that corresponds to each poll_id, and then check if the the 'question_id' also corresponds, and the sample size
#but there will be multiple entries with each poll_id, question_id etc, so we need to check ALL with matching poll_id and
# keep only those that match all three of a given row in final_matched_set

# It might be easier to identify and append rows

Number of Doubles: 1257
done


In [39]:
#poll_raw_years.index[(poll_raw_years['poll_id']==47324)].tolist()
#len(poll_raw_years_indices)
#final_matched_set
unmatched_entries = []
indices = []
final_matched_set['methodology'] = matching_methodology

for index, row in final_matched_set.iterrows():
    #print(str(row['pollster']) + " : " + str(matching_pollsters[index]))
    if row['pollster'] != matching_pollsters[index]:
        if row['pollster'] not in (matching_pollsters[index]) and matching_pollsters[index] not in (row['pollster']):
            unmatched_entries.append(str(row['pollster']) + " : " + str(matching_pollsters[index]))
            indices.append(index)
        
unmatched = pd.DataFrame({'org_index':indices,
                        'pollsters':unmatched_entries})



unmatched

org_index                                          pollsters
0           5                           IBD/TIPP : TIPP Insights
1           6                    Selzer & Company : Selzer & Co.
2           8                    Selzer & Company : Selzer & Co.
3          13  USC Dornsife/LA Times : University of Southern...
4          16  RKM Research and Communications, Inc. : RKM Re...
..        ...                                                ...
79       1067  Mason-Dixon Polling & Research, Inc. : Mason-D...
80       1102  Mason-Dixon Polling & Research, Inc. : Mason-D...
81       1179                           IBD/TIPP : TIPP Insights
82       1196  USC Dornsife/LA Times : University of Southern...
83       1232  USC Dornsife/LA Times : University of Southern...

[84 rows x 2 columns]

In [40]:
#"Lucid" not in "The Times-Picayune/Lucid"
#unmatched.to_csv('out.csv',index=False)
final_test = final_matched_set.copy()

In [41]:
# of the matched polls this was the only pollster that could not be verified as being the same under both datasets
# we drop it for consistency
final_test = final_test.drop(final_test.loc[final_test['pollster'] == 'University of Denver'].index)
final_test.columns
# this is the final set

Index(['index', 'cycle', 'branch', 'type', 'matchup', 'forecastdate', 'state',
       'startdate', 'enddate', 'pollster', 'grade', 'samplesize', 'population',
       'poll_wt', 'rawpoll_clinton', 'rawpoll_trump', 'rawpoll_johnson',
       'rawpoll_mcmullin', 'adjpoll_clinton', 'adjpoll_trump',
       'adjpoll_johnson', 'adjpoll_mcmullin', 'multiversions', 'url',
       'poll_id', 'question_id', 'createddate', 'timestamp', 'methodology'],
      dtype='object')

In [42]:
#final_test.to_csv('final_test.csv',index=False)

In [43]:
as_data.columns

Index(['state', 'startdate', 'enddate', 'pollster', 'grade', 'samplesize',
       'population', 'rawpoll_clinton', 'rawpoll_trump', 'rawpoll_johnson',
       'rawpoll_mcmullin', 'adjpoll_clinton', 'adjpoll_trump',
       'adjpoll_johnson', 'adjpoll_mcmullin'],
      dtype='object')

In [44]:
assigned_compare = pd.read_csv('polls_us_election_2016.csv')
assigned_compare['startdate'] = assigned_compare['startdate'].astype('datetime64')
assigned_compare['enddate'] = assigned_compare['enddate'].astype('datetime64')

In [45]:
# let's see how many of these are in the original dataset
org_test = final_test.copy()

# take irrelevant columns out to allow testing for equality
unique_cols = assigned_compare.columns.append(org_test.columns).drop_duplicates(keep=False)

org_test = org_test.drop(columns=unique_cols)


# inner join and check size

end = org_test.merge(as_data, 'inner')
len(end['pollster'].unique())
len(final_test['pollster'].unique())
final_test.shape[0]
final_test['methodology'].unique()

array(['Online', 'IVR/Online', 'IVR', 'Live Phone', 'IVR/Live Phone',
       'Mail', 'Live Phone/Online', 'IVR/Live Phone/Text'], dtype=object)

# number of items depending on dataset

- Assigned dataset would have 418 entries
- Origin dataset would have 1254 entries

- of the 418 entries from assigned, there would be 88 unique pollsters (end)
- of the 1254 entries from the whole set, again, 88 are unique. (final_test)
-- go with BIGGER SET, some values are necessary that are not in assigned for identifying and more data points should make better results

## Rethink this if necessary

In [46]:
# Now we will create a bias entry for each using the raw_poll file 'bias' - we will say anywhere over +/-2 is a bias
# negative is bias towards republicans, positive towards democrats
# Wait, would this be meaningless since I'll be looking at preferences based on methodology anyways?
# lets just start by looking at how each method leans

# bar chart, x axis is methodology, dual bar where one is percentage republican, other is percentage dem, 
# and y-axis is the actual percentages (adjusted and raw) - Note: adjusted takes into factors like pollster rating

US_chart = final_test[final_test['state'] == 'U.S.']

chart_US = alt.Chart(US_chart).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(rawpoll_clinton)'),
    color = alt.Color('methodology')
).configure_facet(spacing = 0.3)

chart_all_raw = alt.Chart(final_test).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(rawpoll_clinton)'),
    color = alt.Color('methodology')
).configure_facet(spacing = 0.3)

chart_all_adj = alt.Chart(final_test).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(adjpoll_clinton)'),
    color = alt.Color('methodology')
).configure_facet(spacing = 0.3)

chart_all_adj.display()

alt.Chart(...)

### drop all of 'IVR/Live Phone/Text' and 'Mail'
### drop states where only one methodology
### States with only one:

- Alabama - Online
- Connecticut - Online
- Delaware - Online
- DC - Online
- Hawaii - Online
- Maryland - Online
- Mississippi - Online
- Montana - Online
- Nebraska - Online
- Nebraska CD-2 (second congressional district) - Live Phone
- North Dakota - Online
- Rhode Island - Online
- Tennessee - Online
- West Virginia - Online
- Wyoming - Online

## NOTE: IVR is over the phone so might want to combine with Live Phone

In [47]:
cut_down_data = final_test.copy()
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['methodology'] == 'IVR/Live Phone/Text'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['methodology'] == 'Mail'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Alabama'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Connecticut'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Delaware'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'District of Columbia'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Hawaii'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Maryland'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Mississippi'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Montana'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Nebraska'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Nebraska CD-2'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'North Dakota'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Rhode Island'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Tennessee'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'West Virginia'].index)
cut_down_data = cut_down_data.drop(cut_down_data.loc[cut_down_data['state'] == 'Wyoming'].index)

#cut_down_data

In [111]:
# Build a set of ONLY the swing states
cut_down_swing = cut_down_data.copy()

cut_down_swing = cut_down_swing[cut_down_swing['state'] == 'Arizona']
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'Colorado'])
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'Florida'])
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'Iowa'])
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'Michigan'])
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'Nevada'])
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'New Hampshire'])
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'North Carolina'])
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'Ohio'])
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'Pennsylvania'])
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'Virginia'])
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'Wisconsin'])
cut_down_swing = cut_down_swing.append(cut_down_data[cut_down_data['state'] == 'U.S.'])


#cut_down_swing

In [133]:
swings = cut_down_swing['state'].unique()
pres_pop_pct_clinton = [0]*cut_down_swing.shape[0]
pres_pop_pct_trump = [0]*cut_down_swing.shape[0]
i = 0

for index,row in cut_down_swing.iterrows():
    
    pres_pop_pct_clinton[i] = pres_pop.loc[row['state'],'Clinton_Pct']
    pres_pop_pct_trump[i] = pres_pop.loc[row['state'],'Trump_Pct']
    i += 1
 


In [141]:
cut_down_swing['Clinton_Pct_Elec'] = pres_pop_pct_clinton
cut_down_swing['Trump_Pct_Elec'] = pres_pop_pct_trump
#cut_down_swing

chart_all_cut_adj = alt.Chart(cut_down_data).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(adjpoll_clinton)'),
    color = alt.Color('methodology')
).configure_facet(spacing = 0.3)

chart_all_cut_adj

chart_all_cut_raw = alt.Chart(cut_down_data).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(rawpoll_clinton)'),
    color = alt.Color('methodology')
).configure_facet(spacing = 0.3)

chart_all_cut_raw

In [144]:
# Only IVR, Live Phone, Online
ivr_phone_online = cut_down_data.copy()

ivr_phone_online = ivr_phone_online.drop(ivr_phone_online.loc[cut_down_data['methodology'] == 'IVR/Live Phone'].index)
ivr_phone_online = ivr_phone_online.drop(ivr_phone_online.loc[cut_down_data['methodology'] == 'IVR/Online'].index)
ivr_phone_online = ivr_phone_online.drop(ivr_phone_online.loc[cut_down_data['methodology'] == 'Live Phone/Online'].index)

#ivr_phone_online

ivr_phone_online_chart_raw = alt.Chart(ivr_phone_online).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(rawpoll_clinton)'),
    color = alt.Color('methodology')
).configure_facet(spacing = 5)

ivr_phone_online_chart_raw

ivr_phone_online_chart_adj = alt.Chart(ivr_phone_online).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(adjpoll_clinton)'),
    color = alt.Color('methodology')
).configure_facet(spacing = 5)

ivr_phone_online_chart_adj

In [147]:
ivr_phone_online_swing = cut_down_swing.copy()

#ivr_phone_online_swing = ivr_phone_online_swing.drop(ivr_phone_online_swing.loc[cut_down_swing['methodology'] == 'IVR/Live Phone'].index)
ivr_phone_online_swing = ivr_phone_online_swing.drop(ivr_phone_online_swing.loc[cut_down_swing['methodology'] == 'IVR/Online'].index)
ivr_phone_online_swing = ivr_phone_online_swing.drop(ivr_phone_online_swing.loc[cut_down_swing['methodology'] == 'Live Phone/Online'].index)

#ivr_phone_online_swing


ivr_phone_online_chart_swing_adj = alt.Chart(ivr_phone_online_swing).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(adjpoll_clinton)'),
    color = alt.Color('methodology')
).configure_facet(spacing = 5)

ivr_phone_online_chart_swing_adj

ivr_phone_online_chart_swing_raw = alt.Chart(ivr_phone_online_swing).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(rawpoll_clinton)'),
    color = alt.Color('methodology')
).configure_facet(spacing = 5)

ivr_phone_online_chart_swing_raw

three_trump_chart_swing_raw = alt.Chart(ivr_phone_online_swing).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(rawpoll_trump)'),
    color = alt.Color('methodology')
).configure_facet(spacing = 5)

three_trump_chart_swing_raw

three_trump_chart_swing_adj = alt.Chart(ivr_phone_online_swing).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(adjpoll_trump)'),
    color = alt.Color('methodology')
).configure_facet(spacing = 5)

three_trump_chart_swing_adj

In [152]:
#final_test[final_test['methodology'] == 'Online']
final_test.columns

Index(['index', 'cycle', 'branch', 'type', 'matchup', 'forecastdate', 'state',
       'startdate', 'enddate', 'pollster', 'grade', 'samplesize', 'population',
       'poll_wt', 'rawpoll_clinton', 'rawpoll_trump', 'rawpoll_johnson',
       'rawpoll_mcmullin', 'adjpoll_clinton', 'adjpoll_trump',
       'adjpoll_johnson', 'adjpoll_mcmullin', 'multiversions', 'url',
       'poll_id', 'question_id', 'createddate', 'timestamp', 'methodology'],
      dtype='object')

In [153]:
# Combine IVR and Live Phone -> into Phone Based

phone_online_swing = ivr_phone_online_swing.copy()

phone_online_swing.loc[phone_online_swing['methodology'] == 'IVR','methodology'] = 'Phone'
phone_online_swing.loc[phone_online_swing['methodology'] == 'Live Phone','methodology'] = 'Phone'
phone_online_swing.loc[phone_online_swing['methodology'] == 'IVR/Live Phone','methodology'] = 'Phone'

#phone_online_swing['methodology']

In [192]:
# Remove all nan grades

phone_online_swing = phone_online_swing[phone_online_swing['grade'].notna()]
phone_online_swing['grade'].unique()

array(['C-', 'B', 'A+', 'C', 'B+', 'C+', 'B-', 'A-', 'A'], dtype=object)

array(['B', 'A+', 'B+', 'A-', 'A'], dtype=object)

In [188]:
phone_online_chart_swing_raw_clint = alt.Chart(phone_online_swing).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(rawpoll_clinton)'),
    color = alt.Color('methodology')
)#.configure_facet(spacing = 5)

phone_online_chart_swing_raw_clint

alt.Chart(...)

In [189]:
phone_online_chart_swing_raw_trump = alt.Chart(phone_online_swing).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(rawpoll_trump)'),
    color = alt.Color('methodology')
)#.configure_facet(spacing = 5)

phone_online_chart_swing_raw_trump

alt.Chart(...)

phone_online_chart_swing_adj_clint = alt.Chart(phone_online_swing).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(adjpoll_clinton)'),
    color = alt.Color('methodology')
)#.configure_facet(spacing = 5)

phone_online_chart_swing_adj_clint

phone_online_chart_swing_adj_trump = alt.Chart(phone_online_swing).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(adjpoll_trump)'),
    color = alt.Color('methodology')
)#.configure_facet(spacing = 5)

phone_online_chart_swing_adj_trump

In [283]:
## BELOW HERE RESULTS OF ONLY GOOD POLLS (B graded and above)
# Remove all grades under a B:  {B-,C+,C, C-}
phone_online_swing_good = phone_online_swing.copy()
#phone_online_swing_good = phone_online_swing_good[~phone_online_swing_good['grade'].isin(['B-','C+','C', 'C-'])]

# Drop states with no 

phone_online_swing_good['grade'].unique()

array(['C-', 'B', 'A+', 'C', 'B+', 'C+', 'B-', 'A-', 'A'], dtype=object)

In [284]:
# remove states with missing data

phone_online_swing_good = phone_online_swing_good.drop(phone_online_swing_good.loc[phone_online_swing_good['state'] == 'Iowa'].index)
phone_online_swing_good = phone_online_swing_good.drop(phone_online_swing_good.loc[phone_online_swing_good['state'] == 'Michigan'].index)
phone_online_swing_good = phone_online_swing_good.drop(phone_online_swing_good.loc[phone_online_swing_good['state'] == 'Nevada'].index)
phone_online_swing_good = phone_online_swing_good.drop(phone_online_swing_good.loc[phone_online_swing_good['state'] == 'Virginia'].index)
phone_online_swing_good = phone_online_swing_good.drop(phone_online_swing_good.loc[phone_online_swing_good['state'] == 'Wisconsin'].index)


In [285]:
phone_online_swing_good_raw_clint = alt.Chart(phone_online_swing_good).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(rawpoll_clinton)'),
    color = alt.Color('methodology')
)#.configure_facet(spacing = 5)

phone_online_swing_good_raw_clint

alt.Chart(...)

In [286]:
phone_online_swing_good_raw_trump = alt.Chart(phone_online_swing_good).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(rawpoll_trump)'),
    color = alt.Color('methodology')
)#.configure_facet(spacing = 5)

phone_online_swing_good_raw_trump

alt.Chart(...)

phone_online_swing_good_adj_clint = alt.Chart(phone_online_swing_good).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(adjpoll_clinton)'),
    color = alt.Color('methodology')
)#.configure_facet(spacing = 5)

phone_online_swing_good_adj_clint

phone_online_swing_good_adj_trump = alt.Chart(phone_online_swing_good).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('methodology'),
    y = alt.Y('mean(adjpoll_trump)'),
    color = alt.Color('methodology')
)#.configure_facet(spacing = 5)

phone_online_swing_good_adj_trump

test1 = phone_online_swing_good[phone_online_swing_good['methodology'] == 'Phone']
test1['adjpoll_trump'].mean()

test2 = phone_online_swing_good[phone_online_swing_good['methodology'] == 'Online']
test2['adjpoll_trump'].mean()

test1['adjpoll_clinton'].mean()

test2['adjpoll_clinton'].mean()

In [287]:
# phone
test1['rawpoll_trump'].mean()
# online
test2['rawpoll_trump'].mean()
# phone
test1['rawpoll_clinton'].mean()
# online
test2['rawpoll_clinton'].mean()

43.20315789473684

In [288]:
# Drop Colorado and New Hampshire - comment out if want them######################
phone_online_swing_good = phone_online_swing_good.drop(phone_online_swing_good.loc[phone_online_swing_good['state'] == 'Colorado'].index)
phone_online_swing_good = phone_online_swing_good.drop(phone_online_swing_good.loc[phone_online_swing_good['state'] == 'New Hampshire'].index)


In [289]:
# Final Dataset and Visualizations (?) - before making pretty


# I want to insert a column on each graph with the actual result -- how to do
## Make new set with mean of each raw set for each relevant state as column entry and a third column for final results

phone_data = phone_online_swing_good[phone_online_swing_good['methodology'] == 'Phone']
online_data = phone_online_swing_good[phone_online_swing_good['methodology'] == 'Online']

list_of_states = phone_online_swing_good['state'].unique().tolist()
trump_phone_mean = [0]*len(list_of_states)
trump_online_mean = [0]*len(list_of_states)
trump_final_percent = [0]*len(list_of_states)

clinton_phone_mean = [0]*len(list_of_states)
clinton_online_mean = [0]*len(list_of_states)
clinton_final_percent = [0]*len(list_of_states)

for i in range(len(list_of_states)):
    curr_set_phone = phone_data[phone_data['state'] == list_of_states[i]]
    curr_set_online = online_data[online_data['state'] == list_of_states[i]]
    
    trump_phone_mean[i] = curr_set_phone['rawpoll_trump'].mean()
    trump_online_mean[i] = curr_set_online['rawpoll_trump'].mean()
    clinton_phone_mean[i] = curr_set_phone['rawpoll_clinton'].mean()
    clinton_online_mean[i] = curr_set_online['rawpoll_clinton'].mean()
    trump_final_percent[i] = phone_online_swing_good[phone_online_swing_good['state'] == list_of_states[i]]['Trump_Pct_Elec'].mean()
    clinton_final_percent[i] = phone_online_swing_good[phone_online_swing_good['state'] == list_of_states[i]]['Clinton_Pct_Elec'].mean()


## with colorado and new hampshire

fin_df = pd.DataFrame({'state':list_of_states,
                       'trump_phone_pct':trump_phone_mean,
                      'clinton_phone_pct':clinton_phone_mean,
                      'trump_online_pct':trump_online_mean,
                      'clinton_online_pct':clinton_online_mean,
                      'trump_elect_pct':trump_final_percent,
                      'clinton_elect_pct':clinton_final_percent,
                      'won_by_pop': ['Donald Trump', 'Hillary Clinton', 'Donald Trump', 'Hillary Clinton', 
                                 'Donald Trump', 'Donald Trump', 'Donald Trump', 'Hillary Clinton'],
                      'won_by_seats':['Donald Trump', 'Hillary Clinton', 'Donald Trump', 'Hillary Clinton', 
                                 'Donald Trump', 'Donald Trump', 'Donald Trump', 'Donald Trump'],
                      'num_seats_winner': [11,9,29,4,15,18,20,304]})

fin_df

In [290]:
# Without Colorado and New Hampshire
## with colorado and new hampshire

fin_df = pd.DataFrame({'state':list_of_states,
                       'trump_phone_pct':trump_phone_mean,
                      'clinton_phone_pct':clinton_phone_mean,
                      'trump_online_pct':trump_online_mean,
                      'clinton_online_pct':clinton_online_mean,
                      'trump_elect_pct':trump_final_percent,
                      'clinton_elect_pct':clinton_final_percent,
                      'won_by_pop': ['Donald Trump', 'Donald Trump', 
                                 'Donald Trump', 'Donald Trump', 'Donald Trump', 'Hillary Clinton'],
                      'won_by_seats':['Donald Trump', 'Donald Trump',
                                 'Donald Trump', 'Donald Trump', 'Donald Trump', 'Donald Trump'],
                      'num_seats_winner': [11,29,15,18,20,304]})

fin_df

state  trump_phone_pct  clinton_phone_pct  trump_online_pct  \
0         Arizona        46.500000          44.000000         43.333333   
1         Florida        45.050000          45.318750         44.500000   
2  North Carolina        45.388333          45.693333         43.333333   
3            Ohio        46.035000          43.262500         45.333333   
4    Pennsylvania        43.143000          46.151000         41.750000   
5            U.S.        43.525000          45.500000         39.466250   

   clinton_online_pct  trump_elect_pct  clinton_elect_pct       won_by_pop  \
0           43.333333        48.671616          45.126022     Donald Trump   
1           46.000000        49.021941          47.823316     Donald Trump   
2           47.666667        49.828095          46.172866     Donald Trump   
3           42.333333        51.687651          43.558076     Donald Trump   
4           47.000000        48.183336          47.464949     Donald Trump   
5           43.796250        46.085580          48.184578  Hillary Clinton   

   won_by_seats  num_seats_winner  
0  Donald Trump                11  
1  Donald Trump                29  
2  Donald Trump                15  
3  Donald Trump                18  
4  Donald Trump                20  
5  Donald Trump               304

In [291]:
final_graph_trump = alt.Chart(fin_df).transform_fold(
    ['trump_phone_pct','trump_online_pct','trump_elect_pct']).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('key:N'),
    y = alt.Y('value:Q', scale = alt.Scale(domain = [35,52])),
    color = alt.Color('key:N')
)#.configure_facet(spacing = 5)

final_graph_trump

alt.Chart(...)

In [292]:
final_graph_clinton = alt.Chart(fin_df).transform_fold(
    ['clinton_phone_pct','clinton_online_pct','clinton_elect_pct']).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('key:N'),
    y = alt.Y('value:Q', scale = alt.Scale(domain = [35,52])),
    color = alt.Color('key:N')
)#.configure_facet(spacing = 5)

final_graph_clinton

alt.Chart(...)

In [293]:
# These next two are MIDWAY GRAPHS - not final

final_graph_phone = alt.Chart(fin_df).transform_fold(
    ['trump_phone_pct','clinton_phone_pct']).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('key:N'),
    y = alt.Y('value:Q'),
    color = alt.Color('key:N')
)#.configure_facet(spacing = 5)

final_graph_phone

alt.Chart(...)

In [294]:
final_graph_online = alt.Chart(fin_df).transform_fold(
    ['trump_online_pct','clinton_online_pct']).mark_bar().encode(
    column = alt.Column('state'),
    x = alt.X('key:N'),
    y = alt.Y('value:Q'),
    color = alt.Color('key:N')
)#.configure_facet(spacing = 5)

final_graph_online

alt.Chart(...)

In [295]:
# Look at difference between percentage for phone and online

fin_df['online-phone_trump'] = fin_df['trump_online_pct'] - fin_df['trump_phone_pct']
fin_df['online-phone_clinton'] = fin_df['clinton_online_pct'] - fin_df['clinton_phone_pct']
fin_df

state  trump_phone_pct  clinton_phone_pct  trump_online_pct  \
0         Arizona        46.500000          44.000000         43.333333   
1         Florida        45.050000          45.318750         44.500000   
2  North Carolina        45.388333          45.693333         43.333333   
3            Ohio        46.035000          43.262500         45.333333   
4    Pennsylvania        43.143000          46.151000         41.750000   
5            U.S.        43.525000          45.500000         39.466250   

   clinton_online_pct  trump_elect_pct  clinton_elect_pct       won_by_pop  \
0           43.333333        48.671616          45.126022     Donald Trump   
1           46.000000        49.021941          47.823316     Donald Trump   
2           47.666667        49.828095          46.172866     Donald Trump   
3           42.333333        51.687651          43.558076     Donald Trump   
4           47.000000        48.183336          47.464949     Donald Trump   
5           43.796250        46.085580          48.184578  Hillary Clinton   

   won_by_seats  num_seats_winner  online-phone_trump  online-phone_clinton  
0  Donald Trump                11           -3.166667             -0.666667  
1  Donald Trump                29           -0.550000              0.681250  
2  Donald Trump                15           -2.055000              1.973333  
3  Donald Trump                18           -0.701667             -0.929167  
4  Donald Trump                20           -1.393000              0.849000  
5  Donald Trump               304           -4.058750             -1.703750

In [296]:
# Look at difference between percentage for phone and online
# stretch both to 100% first to get comparable measures

fin_df['online-phone_trump'] = 100 - ((100/fin_df['trump_online_pct'])*fin_df['trump_phone_pct'])
fin_df['online-phone_clinton'] = 100 - ((100/fin_df['clinton_online_pct'])*fin_df['clinton_phone_pct'])
fin_df

state  trump_phone_pct  clinton_phone_pct  trump_online_pct  \
0         Arizona        46.500000          44.000000         43.333333   
1         Florida        45.050000          45.318750         44.500000   
2  North Carolina        45.388333          45.693333         43.333333   
3            Ohio        46.035000          43.262500         45.333333   
4    Pennsylvania        43.143000          46.151000         41.750000   
5            U.S.        43.525000          45.500000         39.466250   

   clinton_online_pct  trump_elect_pct  clinton_elect_pct       won_by_pop  \
0           43.333333        48.671616          45.126022     Donald Trump   
1           46.000000        49.021941          47.823316     Donald Trump   
2           47.666667        49.828095          46.172866     Donald Trump   
3           42.333333        51.687651          43.558076     Donald Trump   
4           47.000000        48.183336          47.464949     Donald Trump   
5           43.796250        46.085580          48.184578  Hillary Clinton   

   won_by_seats  num_seats_winner  online-phone_trump  online-phone_clinton  
0  Donald Trump                11           -7.307692             -1.538462  
1  Donald Trump                29           -1.235955              1.480978  
2  Donald Trump                15           -4.742308              4.139860  
3  Donald Trump                18           -1.547794             -2.194882  
4  Donald Trump                20           -3.336527              1.806383  
5  Donald Trump               304          -10.284104             -3.890173

In [297]:
mb_org_data = pd.read_csv('Dataset_assigned_data_taken_from\\president_general_polls_2016.csv')
# I have the FiveThirtyEight dataset one level deeper than the provided set within the folder laballed above

Import found data from FiveThirtyEight (testing if same dataset but raw)

In [298]:
poll_raw_years

poll_id  question_id  race_id  year            race location  \
8105    47078        73672       94  2016  2016_Pres-G_US       US   
8106    47091        73708       94  2016  2016_Pres-G_US       US   
8107    47097        73719      605  2016  2016_Pres-G_AZ       AZ   
8108    47177        73852      611  2016  2016_Pres-G_FL       FL   
8109    47250        73944      611  2016  2016_Pres-G_FL       FL   
...       ...          ...      ...   ...             ...      ...   
8997    48525        76068      612  2016  2016_Pres-G_GA       GA   
8998    48770        76353      612  2016  2016_Pres-G_GA       GA   
8999    48859        76463      624  2016  2016_Pres-G_MI       MI   
9000    48686        76258      624  2016  2016_Pres-G_MI       MI   
9001    48614        76158      634  2016  2016_Pres-G_NM       NM   

     type_simple type_detail  \
8105      Pres-G      Pres-G   
8106      Pres-G      Pres-G   
8107      Pres-G      Pres-G   
8108      Pres-G      Pres-G   
8109      Pres-G      Pres-G   
...          ...         ...   
8997      Pres-G      Pres-G   
8998      Pres-G      Pres-G   
8999      Pres-G      Pres-G   
9000      Pres-G      Pres-G   
9001      Pres-G      Pres-G   

                                               pollster  pollster_rating_id  \
8105                              Quinnipiac University                 267   
8106                                  Rasmussen Reports                 277   
8107                                       Data Orbital                  73   
8108                              Cherry Communications                  49   
8109                                              Lucid                 175   
...                                                 ...                 ...   
8997  Landmark Communications/Rosetta Stone Communic...                 751   
8998                                    Trafalgar Group                 338   
8999                 Mitchell Research & Communications                 213   
9000                                    Trafalgar Group                 338   
9001                                           Zia Poll                 393   

      ... margin_poll electiondate cand1_actual  cand2_actual margin_actual  \
8105  ...        6.50   2016-11-08        48.54         46.43          2.11   
8106  ...       -3.00   2016-11-08        48.54         46.43          2.11   
8107  ...        0.00   2016-11-08        45.13         48.68         -3.55   
8108  ...        4.00   2016-11-08        47.82         49.02         -1.20   
8109  ...        6.00   2016-11-08        47.82         49.02         -1.20   
...   ...         ...          ...          ...           ...           ...   
8997  ...       -3.00   2016-11-08        45.65         50.78         -5.13   
8998  ...       -6.47   2016-11-08        45.65         50.78         -5.13   
8999  ...        6.00   2016-11-08        47.28         47.50         -0.22   
9000  ...       -1.70   2016-11-08        47.28         47.50         -0.22   
9001  ...        2.00   2016-11-08        48.26         40.04          8.21   

      error  bias  rightcall advancedplusminus  \
8105   4.39  4.39        1.0          0.687305   
8106   5.11 -5.11        0.0          1.493971   
8107   3.55  3.55        0.5         -0.113499   
8108   5.20  5.20        0.0          0.742766   
8109   7.20  7.20        0.0          3.130327   
...     ...   ...        ...               ...   
8997   2.13  2.13        1.0         -0.231477   
8998   1.34 -1.34        1.0         -1.293702   
8999   6.22  6.22        0.0          2.713422   
9000   1.48 -1.48        1.0         -2.566293   
9001   6.21 -6.21        1.0          3.925305   

                                                comment  
8105  average of multiple versions or turnout models...  
8106                                                NaN  
8107                                                NaN  
8108                 for unspecified Republican s

In [299]:
#mb_org_data

In [300]:
#Going to try graph between survey size and rating

fig = alt.Chart(as_data).mark_point().encode(x='grade',y='samplesize')

In [301]:
fplot = fig + fig.transform_regression('grade','samplesize').mark_line()

In [302]:
fplot
# clearly the extreme values are making the visualization worse. Let's see how many counts we have for each 5000 size range 

alt.LayerChart(...)

In [303]:
count = 0

for i in range(0,as_data.shape[0]):
    if as_data.loc[i,'samplesize'] > 10000:
        count += 1
    
print(count)

41


In [304]:
#Only 41 with over 10000, lets try with only sample sizes less than 10000

small_samples = as_data[as_data['samplesize']<10000]

In [305]:
# So seemingly no correlation between grade and sample size
fig2 = alt.Chart(small_samples).mark_point().encode(x='grade',y='samplesize')
fplot2 = fig2 + fig2.transform_regression('grade','samplesize').mark_line()
fplot2
# Notice how the 'A+' grade has seemingly smaller samplesizes, suggesting it's possible that better polls are signified
# not by more data, but instead by better practices in adjusting the data

alt.LayerChart(...)

datetime_object = dt.strptime(as_data.loc[1,'enddate'], '%Y-%m-%d')
datetime_object

as_data['startdate'] = as_data['startdate'].astype('datetime64')
as_data['enddate'] = as_data['enddate'].astype('datetime64')

In [306]:
as_data.loc[1,'enddate']-as_data.loc[1,'startdate']

Timedelta('6 days 00:00:00')

In [307]:
#Finding longest observation range
max_delt = as_data.loc[0,'enddate']-as_data.loc[0,'startdate']


for i in range(0,as_data.shape[0]):
    curr_delt = as_data.loc[i,'enddate']-as_data.loc[i,'startdate']
    if curr_delt > max_delt:
        max_delt=curr_delt
    
print(max_delt)

59 days 00:00:00



# Possible story to look into, more data DOES NOT EQUAL better results!

### Possible other story to look into - accuracy of polls for 'likely voters' vs 'rv' vs 'a' vs 'v'

- would want to look into how many of each there are, but more importantly, what the distribution of poll grades is within each

#This will make a 'timedelta64' type column with length of survey
#Adding column of length of survey
lengthofsurvey = [0]*as_data.shape[0]

for i in range(0,as_data.shape[0]):
    lengthofsurvey[i] = as_data.loc[i,'enddate']-as_data.loc[i,'startdate']
    
as_data['lengthofsurvey'] = lengthofsurvey
#as_data['lengthofsurvey']

In [308]:
#Adding column of length of survey (days_integer)
lengthofsurvey = [0]*as_data.shape[0]

for i in range(0,as_data.shape[0]):
    lengthofsurvey[i] = (as_data.loc[i,'enddate']-as_data.loc[i,'startdate']).total_seconds()/(60*60*24)
    
as_data['lengthofsurveydaysint'] = lengthofsurvey
#as_data = as_data.drop(columns = ['lengthofsurvey'])
#as_data = as_data.drop(columns = ['lengthofsurvey_days_int'])
#(as_data.loc[1, 'lengthofsurvey']).total_seconds()/(60*60*24)

In [309]:
alt.Chart(as_data).mark_bar().encode(
    alt.X("lengthofsurveydaysint:Q", bin=alt.Bin(extent=[0,60],step=4), title='Length of Survey (Days)'), 
                                     alt.Y('count()', title = 'Number of Surveys')
                                    )


alt.Chart(...)

In [310]:
as_data

state  startdate    enddate                  pollster grade  \
0          U.S. 2016-11-03 2016-11-06  ABC News/Washington Post    A+   
1          U.S. 2016-11-01 2016-11-07   Google Consumer Surveys     B   
2          U.S. 2016-11-02 2016-11-06                     Ipsos    A-   
3          U.S. 2016-11-04 2016-11-07                    YouGov     B   
4          U.S. 2016-11-03 2016-11-06          Gravis Marketing    B-   
...         ...        ...        ...                       ...   ...   
4203   Virginia 2016-09-16 2016-09-22                     Ipsos    A-   
4204  Wisconsin 2016-08-04 2016-08-07      Marquette University     A   
4205       Utah 2016-11-01 2016-11-07   Google Consumer Surveys     B   
4206     Oregon 2016-10-21 2016-11-02                     Ipsos    A-   
4207   Michigan 2016-01-23 2016-01-26                  EPIC-MRA    A-   

      samplesize population  rawpoll_clinton  rawpoll_trump  rawpoll_johnson  \
0         2220.0         lv            47.00          43.00             4.00   
1        26574.0         lv            38.03          35.69             5.46   
2         2195.0         lv            42.00          39.00             6.00   
3         3677.0         lv            45.00          41.00             5.00   
4        16639.0         rv            47.00          43.00             3.00   
...          ...        ...              ...            ...              ...   
4203       452.0         lv            46.54          40.04              NaN   
4204       683.0         lv            47.00          34.00             9.00   
4205       286.0         lv            21.33          35.05             9.99   
4206       446.0         lv            46.46          37.41              NaN   
4207       600.0         lv            43.00          41.00              NaN   

      rawpoll_mcmullin  adjpoll_clinton  adjpoll_trump  adjpoll_johnson  \
0                  NaN         45.20163       41.72430         4.626221   
1                  NaN         43.34557       41.21439         5.175792   
2                  NaN         42.02638       38.81620         6.844734   
3                  NaN         45.65676       40.92004         6.069454   
4                  NaN         46.84089       42.33184         3.726098   
...                ...              ...            ...              ...   
4203               NaN         46.47852       40.48017              NaN   
4204               NaN         48.74781       39.07778         4.705020   
4205               NaN         26.65200       40.57738         9.705791   
4206               NaN         45.12949       37.10720              NaN   
4207               NaN         42.14966       42.05508              NaN   

      adjpoll_mcmullin  lengthofsurveydaysint  
0                  NaN                    3.0  
1                  NaN                    6.0  
2                  NaN                    4.0  
3                  NaN                    3.0  
4                  NaN                    3.0  
...                ...                    ...  
4203               NaN                    6.0  
4204               NaN                    3.0  
4205               NaN                    6.0  
4206               NaN                   12.0  
4207               NaN                    3.0  

[4208 rows x 16 columns]